# <center>Simulación de SDEs</center>

In [ ]:
import numpy as np
import plotly.graph_objects as go

## Algoritmo de Euler-Maruyama

In [8]:
def euler_maruyama(x0, drift, diffusion, T, N=1000):
    dt = T/N
    t = np.linspace(0, T, N+1)
    x = np.zeros(N+1)
    x[0] = x0
    for i in range(N):
        dW = np.sqrt(dt) * np.random.normal()
        x[i+1] = x[i] + drift(x[i], t[i]) * dt + diffusion(x[i], t[i]) * dW
    return t, x

In [9]:
def plot_sde(t, x, title):
    
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=t, y=x, mode='lines', name='Puente Browniano', line=dict(color='royalblue', width=2)))
    
    fig.update_layout(
        title=title,
        xaxis_title='Tiempo (t)',
        yaxis_title='x(t)',
        font=dict(family="Arial", size=14),
        plot_bgcolor='white',
        hovermode='x unified',
        legend=dict(x=0.02, y=0.98),
        width=800,
        height=500,
    )
    fig.update_xaxes(showgrid=True, gridwidth=1, gridcolor='lightgray')
    fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgray')
    
    return fig

### SDE asociada a DDPM

Se considerará como función de varianza $\beta_t$ a una interpolación lineal entre dos valores $\beta_{\operatorname{min}}$ y $\beta_{\operatorname{max}}$.

In [ ]:
x0 = np.random.randn(1)
T = 1000

def beta(t, beta_min = 0.1, beta_max=0.9, t_max=T):
    return beta_min + t/T * (beta_max - beta_min)

drift = lambda x, t: -1/2 * beta(t) * x
diffusion = lambda x, t: np.sqrt(beta(t))

t, x = euler_maruyama(x0, drift, diffusion, T=T, N=100000)
    
# Gráfico:
fig = plot_sde(t, x, title='Simulación de la SDE asociada a DDPM')
fig.show()


### Proceso de Ornstein-Uhlenbeck

In [ ]:
def ornstein_uhlenbeck(x0, T, N, alpha=2, mu=1, sigma=1):
    dt = T / N
    t = np.linspace(0, T, N+1)
    x = np.zeros((5, N+1))
    x[:, 0] = x0
    
    for i in range(5):
        for j in range(N):
            dW = np.random.normal(0, np.sqrt(dt))
            x[i, j+1] = x[i, j] + alpha * (mu - x[i, j]) * dt + sigma * dW
    
    return t, x

# Ejemplo:
x0 = 10
T = 20
N = 1000

t, x = ornstein_uhlenbeck(x0, T, N)

fig = go.Figure()

for i in range(5):
    fig.add_trace(go.Scatter(x=t, y=x[i], mode='lines', name=f'Muestra {i+1}'))

fig.update_layout(
    xaxis_title='Tiempo',
    yaxis_title='X(t)',
    plot_bgcolor='white',
    legend_title='Trayectorias',
    width=1000,
    height=600
)

fig.show()

## Puente browniano

El puente browiano es un proceso estocástico $(X_t)_{t\in[0,T]}$ que sea un movimiento browniano estándar condicionado a que $X_0=x_0$ y $X_T=x_T$, donde $x_0$ y $x_T$ son puntos específicos y $T>0$ es un tiempo fijo.

Este puente está asociado a la siguiente SDE:

$$
dX_t = \frac{x_T-X_t}{T-t}dt + dW_t, \quad X_0=x_0
$$

donde $(W_t)_{t\geq 0}$ es un movimiento browniano estándar.

In [ ]:
def brownian_bridge(x0, xT, T):

    # Puente browniano:
    drift = lambda x, t: (xT - x) / (T - t)
    diffusion = lambda x, t: 1
    t, x = euler_maruyama(x0, drift, diffusion, T=T)
    
    # Gráfico:
    fig = plot_sde(t, x, title='Simulación de Puente Browniano')
    fig.add_trace(go.Scatter(x=[0, T], y=[x0, xT], mode='markers', name='Puntos de anclaje', marker=dict(size=10, color='red', symbol='star')))
    fig.show()

# Ejemplo de uso:
brownian_bridge(x0=2, xT=5, T=1)